# Двумерный градиентный спуск - визуализация

## Импортируем нужные библиотеки

In [1]:
from random import uniform
import numpy as np
import pandas as pd
import plotly.graph_objects as go

### Визуализации

In [2]:
def plot_surface(func):
    x = np.linspace(0, 100, 100).reshape(1, -1)
    y = np.linspace(0, 100, 100).reshape(1, -1)
    f = np.array([[func(x_i, y_j) for y_j in y[0]] for x_i in x[0]])

    layout = go.Layout(scene=dict(aspectmode='cube'))


    fig = go.Figure(data=[go.Surface(z=f)], layout=layout, )

    legend=dict(font=dict(size=12), x=0.45, y=0.95,)

    fig.update_layout(autosize=True,
                      width=800, height=500,
                      margin=dict(l=0, r=50, b=100, t=0),
                      legend=legend,
                      )
    
    return fig

    
def plot_gradient_descent_steps(fig, x_steps, y_steps, func_steps):
    steps = go.Scatter3d(x=x_steps,
                             y=y_steps,
                             z=func_steps,
                             mode='lines+markers',
                             marker=dict(
                                        size=5,
                                        color='red',
                                        colorscale='Viridis',
                             ),
                            line=dict(
                                color='red',
                                width=2
                            )
                        )
    fig.add_trace(steps)
    fig.show()
    return steps
    

## Целевая функция

Можно написать иные `func_2`, `func_3`, и тд,  чтобы поэкспериментировать с ними.

In [3]:
def func_1(x, y):
    # смещаем начало координат в точку (50, 50). чтобы поверхность отображалась в нужном месте
    x -= 50
    y -= 50
    
    return x ** 2 + y ** 2

plot_surface(func_1)

### Вычислим градиент


Сейчас большинство библиотек для машинного обучения, реализуют автоматическое дифферецирование. Однако, мы его использовать не будем, а напишем свою простую функцию, приближенно вычисляющую градиент в точке.

**Комментарий 1.** У вас может возникнуть желание написать в этом месте частную производную конкретной `func_1`, которую мы определили выше. Однако в этом задании предлагается реализовать `gradient_finite_diff` таким образом, чтобы она не зависела от функции f, которая передается в аргментов. Достичь этого можно, вычисляя значения `df_dx` и `df_dy` по формуле аналогичной общей формуле частых производных, в которых используются конечные приращения `dx` и `dy`.

**Комментарий 2.** Начиная с этого момента рекомендуем внимательно читать весь код: ваших знаний достаточно, чтобы понять его полностью.

In [4]:
# в аргументах передаются:
#
#     f -- функция зависящая от двух переменных
#     x0, y0 -- точка, в которой требуется вычислить градиент
#
# опционально можно указать:
#     dx, dy -- дельты по направлениям

def gradient_finite_diff(f, x0, y0, dx=0.0001, dy=0.0001):
    # частная производная по направлению оси х
    df_dx = (f(x0+dx, y0)-f(x0,y0))/dx
    
    # частная производная по направлению оси у
    df_dy = (f(x0, y0+dy)-f(x0,y0))/dy 
    
    return (df_dx, df_dy)

### Градиентный спуск

`gradient_descent` не привязан к конкретной функции, который мы рассматриваем. Формула работает для любой функции, которую можно описать функцией. Аргументы `f`, `x0`, `y0` и тд передаются в функцию извне.

In [5]:
eps = 0.001

def grad_norm(grad):
    return (grad[0] ** 2 + grad[1] ** 2) ** (1/2)


# в аргументах передаются:
#
#     f -- функция зависящая от двух переменных
#
# опционально можно указать:
#
#     (x0, y0) -- точка, с которой будет стартовать градиентный спуск, по умолчанию выбирается случайная точка
#     learning_rate -- размер шага градиентного спуска
#     max_steps_number -- максимальное число шагов градиентного спуска
#     plot -- рисовать ли график


def gradient_descent(f,
                     x0=uniform(0, 100),
                     y0=uniform(0, 100),
                     learning_rate=0.1,
                     max_steps_number=10000,
                     plot=True):
    # рисуем поверхность
    if plot:
        fig = plot_surface(f)
    
    # cтартуем с (x0, y0)
    step_number = 0
    x = x0
    y = y0
    
    # сохраняем последовательность наших шагов
    steps_x = [x0]
    steps_y = [y0]
    steps_func = [f(x0, y0)]
    
    # критерий остановки градиентного спуска:
    #        либо градиент становится близким к 0
    #        либо сделано максимальное число шагов
    while step_number < max_steps_number and grad_norm(gradient_finite_diff(f, x, y)) > eps:
        # вычисляем градиент (получаем вектор с двумя компонентами, он понадобится в шаге градиентного спуска)
        grad = gradient_finite_diff(f, x, y)
        
        # шаг градиентного спуска
        x -= grad[0]*learning_rate
        y -= grad[1]*learning_rate

        # добавляем новую точку и значение в ней в список шагов
        steps_x.append(x)
        steps_y.append(y)
        steps_func.append(f(x, y))
        
        step_number += 1
    
    if plot:
        plot_gradient_descent_steps(fig, steps_x, steps_y, steps_func)
        
    if len(steps_x) == max_steps_number:
        print(f"gradient descent reached maximum number of steps, which is set to {max_steps_number}")
    else:
        print(f"gradient descent terminated after {(step_number + 1)} steps")

    print(f"terminal point of gradient descent is (%.10f, %.10f) with function value %.10f" % (steps_x[-1], steps_y[-1], steps_func[-1]))

## Эксперименты

Поэкспериментируйте с learning rate, начальной точкой.

In [6]:
gradient_descent(func_1, x0=0, y0=100, learning_rate=0.9)

gradient descent terminated after 55 steps
terminal point of gradient descent is (49.9996577000, 50.0002423006) with function value 0.0000001759


In [7]:
gradient_descent(func_1, x0=0, y0=100, learning_rate=0.99)

gradient descent terminated after 589 steps
terminal point of gradient descent is (49.9996033413, 50.0002966594) with function value 0.0000002453


In [8]:
gradient_descent(func_1, x0=0, y0=100, learning_rate=0.999)

gradient descent terminated after 5925 steps
terminal point of gradient descent is (49.9995965758, 50.0003034249) with function value 0.0000002548


In [9]:
gradient_descent(func_1, x0=0, y0=100, learning_rate=1)

gradient descent terminated after 10001 steps
terminal point of gradient descent is (-0.0000005639, 100.0000008185) with function value 5000.0001382432


In [10]:
gradient_descent(func_1, x0=0, y0=100, learning_rate=.01)

gradient descent terminated after 589 steps
terminal point of gradient descent is (49.9996033413, 50.0002966594) with function value 0.0000002453
